In [1]:
import numpy as np
import pandas as pd
import torch
import torch.nn as nn
import torch.nn.parallel
import torch.optim as optim
import torch.utils.data
from torch.autograd import Variable

In [2]:
training_set = pd.read_csv('ml-100k/u1.base', delimiter = '\t')
training_set = np.array(training_set, dtype = 'int')
test_set = pd.read_csv('ml-100k/u1.test', delimiter = '\t')
test_set = np.array(test_set, dtype = 'int')

In [3]:
n_users=int(max(max(training_set[:,0]),max(test_set[:,0])))
n_movies=int(max(max(training_set[:,1]),max(test_set[:,1])))

In [4]:
def convert(data):
    new_data=[]
    for id_user in range(1,n_users+1):
        id_movies=data[:,1][data[:,0]==id_user]
        id_rating=data[:,2][data[:,0]==id_user]
        ratings=np.zeros(n_movies)
        ratings[id_movies-1] = id_rating
        new_data.append(list(ratings))
    return new_data

In [5]:
training_set = convert(training_set)
test_set = convert(test_set)

In [6]:
training_set=torch.FloatTensor(training_set)
test_set=torch.FloatTensor(test_set)

In [7]:
class SAE(nn.Module):
    def __init__(self,):
        super(SAE,self).__init__()
        self.fc1=nn.Linear(n_movies,20)
        self.fc2=nn.Linear(20,10)
        self.fc3=nn.Linear(10,20)
        self.fc4=nn.Linear(20,n_movies)
        self.activation=nn.Sigmoid()
    def forward(self,x):
        x=self.activation(self.fc1(x))
        x=self.activation(self.fc2(x))
        x=self.activation(self.fc3(x))
        x=self.fc4(x)
        return x
        

In [8]:
sae=SAE()
criterion=nn.MSELoss()
optimizer=optim.RMSprop(sae.parameters(),lr=0.01,weight_decay=0.5)

In [9]:
nb_epoch=200
for epoch in range(1,nb_epoch+1):
    train_loss=0
    s=0.
    for id_user in range(n_users):
        input = Variable(training_set[id_user]).unsqueeze(0)
        target = input.clone()
        if torch.sum(target.data>0)>0:
            output = sae(input)
            target.requires_grad=False
            output[target==0]=0
            loss=criterion(output,target)
            mean_corrector=n_movies/float(torch.sum(target.data>0)+1e-10)
            loss.backward()
            train_loss += np.sqrt(loss.data[0]*mean_corrector)
            s+=1.
            optimizer.step()
        print('epoch: '+str(epoch)+' loss: '+str(train_loss/s))


epoch: 1 loss: 3.87320908006
epoch: 1 loss: 3.91411666992
epoch: 1 loss: 3.69697047448
epoch: 1 loss: 3.88323703771
epoch: 1 loss: 3.75696342848
epoch: 1 loss: 3.74624142196
epoch: 1 loss: 3.78504883898
epoch: 1 loss: 3.77991200833
epoch: 1 loss: 3.83142565878
epoch: 1 loss: 3.86753436769
epoch: 1 loss: 3.84232925797
epoch: 1 loss: 3.87344799871
epoch: 1 loss: 3.8359655974
epoch: 1 loss: 3.86311240499
epoch: 1 loss: 3.82068793658
epoch: 1 loss: 3.8511308137
epoch: 1 loss: 3.81584724022
epoch: 1 loss: 3.82069732369
epoch: 1 loss: 3.80478574404
epoch: 1 loss: 3.78203474339
epoch: 1 loss: 3.73936806739
epoch: 1 loss: 3.72600337581
epoch: 1 loss: 3.71997159734
epoch: 1 loss: 3.74164583548
epoch: 1 loss: 3.74624047357
epoch: 1 loss: 3.71422696912
epoch: 1 loss: 3.69393177513
epoch: 1 loss: 3.68956349211
epoch: 1 loss: 3.6934368828
epoch: 1 loss: 3.69399672355
epoch: 1 loss: 3.69957997404
epoch: 1 loss: 3.6901712569
epoch: 1 loss: 3.68465228735
epoch: 1 loss: 3.69596585621
epoch: 1 loss: 3.6

epoch: 1 loss: 2.62602436042
epoch: 1 loss: 2.62454894301
epoch: 1 loss: 2.61939912323
epoch: 1 loss: 2.61703977109
epoch: 1 loss: 2.61533226289
epoch: 1 loss: 2.61217248293
epoch: 1 loss: 2.60941980949
epoch: 1 loss: 2.60759542533
epoch: 1 loss: 2.60559261111
epoch: 1 loss: 2.60395979216
epoch: 1 loss: 2.60496537338
epoch: 1 loss: 2.60258174505
epoch: 1 loss: 2.60068656024
epoch: 1 loss: 2.59782532611
epoch: 1 loss: 2.59506488469
epoch: 1 loss: 2.59198926229
epoch: 1 loss: 2.5892709106
epoch: 1 loss: 2.58732076808
epoch: 1 loss: 2.58507485961
epoch: 1 loss: 2.58145669834
epoch: 1 loss: 2.58090728744
epoch: 1 loss: 2.57701686877
epoch: 1 loss: 2.57367321514
epoch: 1 loss: 2.5721432249
epoch: 1 loss: 2.5724035526
epoch: 1 loss: 2.56973400765
epoch: 1 loss: 2.568194544
epoch: 1 loss: 2.56850524343
epoch: 1 loss: 2.5648751494
epoch: 1 loss: 2.56210906387
epoch: 1 loss: 2.55924589735
epoch: 1 loss: 2.55738312786
epoch: 1 loss: 2.55450814022
epoch: 1 loss: 2.5522694962
epoch: 1 loss: 2.5494

epoch: 1 loss: 2.04445735459
epoch: 1 loss: 2.0430238863
epoch: 1 loss: 2.04131481481
epoch: 1 loss: 2.03975686698
epoch: 1 loss: 2.03806462212
epoch: 1 loss: 2.03673366773
epoch: 1 loss: 2.03536119731
epoch: 1 loss: 2.03465891178
epoch: 1 loss: 2.0336214946
epoch: 1 loss: 2.03256405926
epoch: 1 loss: 2.03069689345
epoch: 1 loss: 2.02934884676
epoch: 1 loss: 2.02781695724
epoch: 1 loss: 2.02604913499
epoch: 1 loss: 2.02609340936
epoch: 1 loss: 2.02461120806
epoch: 1 loss: 2.02303880686
epoch: 1 loss: 2.02142714705
epoch: 1 loss: 2.01999931961
epoch: 1 loss: 2.01842569048
epoch: 1 loss: 2.01691492159
epoch: 1 loss: 2.01551804321
epoch: 1 loss: 2.01431592194
epoch: 1 loss: 2.01327575956
epoch: 1 loss: 2.01209259987
epoch: 1 loss: 2.01085090304
epoch: 1 loss: 2.00942809803
epoch: 1 loss: 2.00909743892
epoch: 1 loss: 2.00808323147
epoch: 1 loss: 2.00752991874
epoch: 1 loss: 2.00581454349
epoch: 1 loss: 2.00419174826
epoch: 1 loss: 2.00234030899
epoch: 1 loss: 2.00223575952
epoch: 1 loss: 2

epoch: 2 loss: 1.12178297004
epoch: 2 loss: 1.12892803442
epoch: 2 loss: 1.12983928879
epoch: 2 loss: 1.1368307251
epoch: 2 loss: 1.13839792054
epoch: 2 loss: 1.1419162905
epoch: 2 loss: 1.14111042888
epoch: 2 loss: 1.13767798026
epoch: 2 loss: 1.13909424213
epoch: 2 loss: 1.1378133477
epoch: 2 loss: 1.13634705637
epoch: 2 loss: 1.13574870269
epoch: 2 loss: 1.13667965892
epoch: 2 loss: 1.13658474494
epoch: 2 loss: 1.1360368491
epoch: 2 loss: 1.13663229724
epoch: 2 loss: 1.13208234525
epoch: 2 loss: 1.13142937009
epoch: 2 loss: 1.12847019257
epoch: 2 loss: 1.12944704932
epoch: 2 loss: 1.12652676151
epoch: 2 loss: 1.12517648521
epoch: 2 loss: 1.12744947166
epoch: 2 loss: 1.1258140339
epoch: 2 loss: 1.12646416943
epoch: 2 loss: 1.12531850759
epoch: 2 loss: 1.12372429075
epoch: 2 loss: 1.12518843837
epoch: 2 loss: 1.127663836
epoch: 2 loss: 1.12589445219
epoch: 2 loss: 1.12524130536
epoch: 2 loss: 1.12381287188
epoch: 2 loss: 1.12190172887
epoch: 2 loss: 1.12521622113
epoch: 2 loss: 1.1270

epoch: 2 loss: 1.11862140097
epoch: 2 loss: 1.11900961609
epoch: 2 loss: 1.11955641827
epoch: 2 loss: 1.11904681855
epoch: 2 loss: 1.11908541384
epoch: 2 loss: 1.11884172767
epoch: 2 loss: 1.11884926717
epoch: 2 loss: 1.1184884524
epoch: 2 loss: 1.11847869219
epoch: 2 loss: 1.11873976511
epoch: 2 loss: 1.11867589675
epoch: 2 loss: 1.11855648674
epoch: 2 loss: 1.11824979144
epoch: 2 loss: 1.11961217803
epoch: 2 loss: 1.11931397443
epoch: 2 loss: 1.11968979759
epoch: 2 loss: 1.11912881908
epoch: 2 loss: 1.11965000658
epoch: 2 loss: 1.1200149674
epoch: 2 loss: 1.12001771452
epoch: 2 loss: 1.11946927885
epoch: 2 loss: 1.1195049097
epoch: 2 loss: 1.11909864958
epoch: 2 loss: 1.11959019701
epoch: 2 loss: 1.1196484603
epoch: 2 loss: 1.1224493699
epoch: 2 loss: 1.12243752047
epoch: 2 loss: 1.12207469558
epoch: 2 loss: 1.12172691059
epoch: 2 loss: 1.12217905404
epoch: 2 loss: 1.12224700642
epoch: 2 loss: 1.12164929186
epoch: 2 loss: 1.12169317418
epoch: 2 loss: 1.12146074649
epoch: 2 loss: 1.12

...

epoch: 199 loss: 0.934335786361
epoch: 199 loss: 0.933635273857
epoch: 199 loss: 0.932776824004
epoch: 199 loss: 0.933790515978
epoch: 199 loss: 0.932046213325
epoch: 199 loss: 0.931531514669
epoch: 199 loss: 0.933336126431
epoch: 199 loss: 0.933925163122
epoch: 199 loss: 0.933666070765
epoch: 199 loss: 0.93311819747
epoch: 199 loss: 0.932300959272
epoch: 199 loss: 0.932649028817
epoch: 199 loss: 0.932956860095
epoch: 199 loss: 0.933438068594
epoch: 199 loss: 0.932923426015
epoch: 199 loss: 0.933974433471
epoch: 199 loss: 0.933000235785
epoch: 199 loss: 0.932761961126
epoch: 199 loss: 0.931416267861
epoch: 199 loss: 0.931063978067
epoch: 199 loss: 0.930837179805
epoch: 199 loss: 0.930764452049
epoch: 199 loss: 0.93183785605
epoch: 199 loss: 0.93145702177
epoch: 199 loss: 0.930833547109
epoch: 199 loss: 0.931895702887
epoch: 199 loss: 0.930759866121
epoch: 199 loss: 0.930452639157
epoch: 199 loss: 0.931168804841
epoch: 199 loss: 0.930759138112
epoch: 199 loss: 0.930575982336
epoch: 199 

epoch: 199 loss: 0.914173890515
epoch: 199 loss: 0.914358163758
epoch: 199 loss: 0.913709247718
epoch: 199 loss: 0.913536558877
epoch: 199 loss: 0.913281673974
epoch: 199 loss: 0.913588761058
epoch: 199 loss: 0.913570865626
epoch: 199 loss: 0.913725934095
epoch: 199 loss: 0.913429324687
epoch: 199 loss: 0.913799456286
epoch: 199 loss: 0.913618394991
epoch: 199 loss: 0.913928651939
epoch: 199 loss: 0.91452801641
epoch: 199 loss: 0.914632380064
epoch: 199 loss: 0.914441119734
epoch: 199 loss: 0.913854290077
epoch: 199 loss: 0.9143417303
epoch: 199 loss: 0.915077318223
epoch: 199 loss: 0.915178022638
epoch: 199 loss: 0.915403204009
epoch: 199 loss: 0.915347351583
epoch: 199 loss: 0.914983150597
epoch: 199 loss: 0.915345644541
epoch: 199 loss: 0.915124537456
epoch: 199 loss: 0.914720571594
epoch: 199 loss: 0.915148665666
epoch: 199 loss: 0.915055216105
epoch: 199 loss: 0.915438506788
epoch: 199 loss: 0.915514014818
epoch: 199 loss: 0.915450074518
epoch: 199 loss: 0.915399946017
epoch: 199 

epoch: 200 loss: 0.936238913185
epoch: 200 loss: 0.950387737445
epoch: 200 loss: 0.947273118672
epoch: 200 loss: 0.952455474039
epoch: 200 loss: 0.942871075697
epoch: 200 loss: 0.940130653896
epoch: 200 loss: 0.955570645776
epoch: 200 loss: 0.954403007931
epoch: 200 loss: 0.960849988403
epoch: 200 loss: 0.951757268132
epoch: 200 loss: 0.945551940239
epoch: 200 loss: 0.92922670216
epoch: 200 loss: 0.917891850667
epoch: 200 loss: 0.914611930465
epoch: 200 loss: 0.911930334507
epoch: 200 loss: 0.905849609802
epoch: 200 loss: 0.905324713317
epoch: 200 loss: 0.904802000991
epoch: 200 loss: 0.90332625978
epoch: 200 loss: 0.892937259138
epoch: 200 loss: 0.916285628231
epoch: 200 loss: 0.914952735599
epoch: 200 loss: 0.920761593226
epoch: 200 loss: 0.918881429359
epoch: 200 loss: 0.930304706468
epoch: 200 loss: 0.936405872405
epoch: 200 loss: 0.938639247128
epoch: 200 loss: 0.935463026521
epoch: 200 loss: 0.936854608112
epoch: 200 loss: 0.93506461554
epoch: 200 loss: 0.932718988346
epoch: 200 

epoch: 200 loss: 0.916085145288
epoch: 200 loss: 0.915383361195
epoch: 200 loss: 0.915005930526
epoch: 200 loss: 0.914608628222
epoch: 200 loss: 0.914769955095
epoch: 200 loss: 0.915535606195
epoch: 200 loss: 0.915208924997
epoch: 200 loss: 0.914170149987
epoch: 200 loss: 0.914584524134
epoch: 200 loss: 0.914106511789
epoch: 200 loss: 0.914479655182
epoch: 200 loss: 0.914131507928
epoch: 200 loss: 0.913844746527
epoch: 200 loss: 0.914709784721
epoch: 200 loss: 0.914498301824
epoch: 200 loss: 0.914378948221
epoch: 200 loss: 0.914168198812
epoch: 200 loss: 0.913839183835
epoch: 200 loss: 0.913960050446
epoch: 200 loss: 0.913725203325
epoch: 200 loss: 0.913632524362
epoch: 200 loss: 0.913332226635
epoch: 200 loss: 0.913133860194
epoch: 200 loss: 0.91283928751
epoch: 200 loss: 0.913222202046
epoch: 200 loss: 0.91311429217
epoch: 200 loss: 0.913701186431
epoch: 200 loss: 0.914069249727
epoch: 200 loss: 0.914866852003
epoch: 200 loss: 0.915085389417
epoch: 200 loss: 0.914568353492
epoch: 200

epoch: 200 loss: 0.917301405103
epoch: 200 loss: 0.917206260652
epoch: 200 loss: 0.917097137308
epoch: 200 loss: 0.917092835718
epoch: 200 loss: 0.917093573774
epoch: 200 loss: 0.91685543013
epoch: 200 loss: 0.917291493603
epoch: 200 loss: 0.917275357168
epoch: 200 loss: 0.917381883175
epoch: 200 loss: 0.917104519093
epoch: 200 loss: 0.916961649576
epoch: 200 loss: 0.916709332342
epoch: 200 loss: 0.916758213708
epoch: 200 loss: 0.917153081496
epoch: 200 loss: 0.917490192176
epoch: 200 loss: 0.917343498873
epoch: 200 loss: 0.917583869634
epoch: 200 loss: 0.917509422913
epoch: 200 loss: 0.917124263259
epoch: 200 loss: 0.917178752617
epoch: 200 loss: 0.917063596358
epoch: 200 loss: 0.917625264549
epoch: 200 loss: 0.918126096297
epoch: 200 loss: 0.918866558156
epoch: 200 loss: 0.918735769825
epoch: 200 loss: 0.918463882157
epoch: 200 loss: 0.918647914417
epoch: 200 loss: 0.918417433931
epoch: 200 loss: 0.917942881656
epoch: 200 loss: 0.918040787423
epoch: 200 loss: 0.917932388752
epoch: 20

In [11]:
test_loss = 0
s = 0.
for id_user in range(n_users):
    input = Variable(training_set[id_user]).unsqueeze(0)
    target = Variable(test_set[id_user])
    if torch.sum(target.data > 0) > 0:
        output = sae(input)
        target.requires_grad=False
        output[target==0]=0
        loss=criterion(output,target)
        mean_corrector=n_movies/float(torch.sum(target.data>0)+1e-10)
        test_loss += np.sqrt(loss.data[0]*mean_corrector)
        s+=1.
    print('loss: '+str(test_loss/s))

loss: 0.995095509354
loss: 0.935396380813
loss: 0.999588269708
loss: 0.893656469815
loss: 0.938500267167
loss: 0.934533777093
loss: 0.94473885617
loss: 0.94200575272
loss: 0.923389187813
loss: 0.900324149252
loss: 0.898638488831
loss: 0.891957754222
loss: 0.922340609615
loss: 0.934032735437
loss: 0.961716685748
loss: 0.959061767541
loss: 0.967038595575
loss: 0.956981964531
loss: 0.954950700215
loss: 0.971814482179
loss: 0.976276645162
loss: 0.985500910218
loss: 0.981192329594
loss: 0.973126411533
loss: 0.964046963911
loss: 0.946300412062
loss: 0.941317181784
loss: 0.936417702995
loss: 0.925078384619
loss: 0.918905054651
loss: 0.920641825097
loss: 0.91444027877
loss: 0.900394012628
loss: 0.903285288321
loss: 0.909506100062
loss: 0.923626284834
loss: 0.926211908888
loss: 0.949309199935
loss: 0.953249012785
loss: 0.957635214182
loss: 0.949957417062
loss: 0.951156659227
loss: 0.95077508321
loss: 0.952318801845
loss: 0.948171274942
loss: 0.946416969145
loss: 0.942797523885
loss: 0.942595766

loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.951060598705
loss: 0.95106